In [3]:
import sys    # 시스템
import os     # 시스템

import pandas as pd    # 판다스 : 데이터분석 라이브러리
import numpy as np     # 넘파이 : 숫자, 행렬 데이터 라이브러리

from selenium import webdriver    # 웹 브라우저 자동화
import time                       # 시간 지연
import math                       # 올림, 내림
from selenium.webdriver.common.keys import Keys
from tqdm import tqdm   # 진행상황 표시

In [4]:
keyword = input('검색어 입력: ')
articles_number = int(input('크롤링 글 개수: '))

In [5]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager


def set_chrome_driver():
    chrome_options = webdriver.ChromeOptions()
    driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=chrome_options)
    return driver

In [6]:
# 스크롤 다운 함수
def scroll_down(driver):
    driver.execute_script("window.scrollTo(0, 99999)")
    time.sleep(2)

In [7]:
from selenium.webdriver.common.by import By

from webdriver_manager.chrome import ChromeDriverManager
# 크롬 웹브라우저 실행
# driver = webdriver.Chrome(ChromeDriverManager().install())
driver = webdriver.Chrome("chromedriver-win64/chromedriver.exe")

# 키워드로 접속
driver.get(f"https://www.youtube.com/results?search_query={keyword}")
time.sleep(2)

# 영상 목록 스크롤 다운 실행
for i in range(math.ceil((articles_number-26)/20)):
    scroll_down(driver)

crawling_list = []
url_list = []

# url 수집
crawling_list = driver.find_elements(By.CSS_SELECTOR, 'h3 > a')

for crawling in crawling_list:
    url = crawling.get_attribute('href')   
    url_list.append(url)
# driver.close()
url_list = url_list[:articles_number]
print('크롤링할 글 수: ', len(url_list))
url_list

C:\Users\Mgyu\AppData\Local\Temp\ipykernel_24556\83369516.py:6: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("chromedriver-win64/chromedriver.exe")


크롤링할 글 수:  10


['https://www.youtube.com/watch?v=W0I6RA92Qj0&pp=ygUG7Jik7YK5',
 'https://www.youtube.com/watch?v=8IKuK_yVkgk&pp=ygUG7Jik7YK5',
 'https://www.youtube.com/watch?v=7r5TPIEaGNk&pp=ygUG7Jik7YK5',
 'https://www.youtube.com/watch?v=gWJ4K-ty6ng&pp=ygUG7Jik7YK5',
 'https://www.youtube.com/shorts/yyvhwfFqKE4',
 'https://www.youtube.com/shorts/MocFKIMBwjM',
 'https://www.youtube.com/shorts/RBFuP909eko',
 'https://www.youtube.com/shorts/K44wfo-xrsI',
 'https://www.youtube.com/watch?v=7wysOQUH1SM&pp=ygUG7Jik7YK5',
 'https://www.youtube.com/watch?v=FMg27cq22wU&pp=ygUG7Jik7YK5']

In [16]:
driver.find_elements(By.CSS_SELECTOR, "#description-interaction")

[<selenium.webdriver.remote.webelement.WebElement (session="93ae00f7c5cf75059d1dae2ec9fb6cba", element="036FDDF83EB1D48AF1F18DAEC029C471_element_101")>]

In [15]:
%%time
dict = {}
count = 0

for url in tqdm(url_list):
    # url 열기
    driver = webdriver.Chrome("chromedriver-win32/chromedriver.exe")
    driver.get(url)
    time.sleep(4)

    driver.execute_script("window.scrollTo(0, 400)")
    time.sleep(1)
    print(1)

    driver.find_elements(By.CSS_SELECTOR, "#description-interaction").click()
    info = driver.find_elements(By.CSS_SELECTOR, '.style-scope ytd-video-primary-info-renderer').text.split('조회수')

    # 제목
    title = info[0].split('\n')[-2]
    
    # 조회수, 날짜 위치 추출
    for i in info[1].split('\n'):
        if '회' in i:
            view_date = i

    # 조회수
    #view = int(view_date[0].split('•')[0].replace('회', '').replace(',',''))
    view = int(view_date.split('•')[0].replace('회', '').replace(',',''))
    # 날짜
    #date = view_date[0].split('•')[1]
    date = view_date.split('•')[1]
    # 좋아요
    like = info[1].split('\n')[1]
    # 싫어요
    dont_like = info[1].split('\n')[2]

    try:
        # 댓글 수
        review_cnt = driver.find_elements(By.XPATH, '/html/body/ytd-app/div/ytd-page-manager/ytd-watch-flexy/div[5]/div[1]/div/ytd-comments/ytd-item-section-renderer/div[1]/ytd-comments-header-renderer/div[1]/h2/yt-formatted-string/span[2]').text.replace(',', '')
        print('<',count,'>', title, '( 댓글 수:', review_cnt,')')
        
        # 댓글 스크롤 다운
        for i in range(math.ceil((int(review_cnt)-20)/20)):
            scroll_down(driver)
        print('1. 스크롤 다운 완료')
        
        # 광고 끄기
        time.sleep(10)
        try:
            driver.find_elements(By.CSS_SELECTOR, "#main > div > ytd-button-renderer").click()
            print('2. 광고 창 제거함')
        except:
            print('2. 광고 창 안뜸')
        
        try:
            # 답글 n개 보기 클릭
            buttons = driver.find_elements(By.CSS_SELECTOR, "#more-replies > a")
            for button in buttons:
                button.send_keys(Keys.ENTER)
                time.sleep(1)
                button.click()
            time.sleep(1)
            print('3. 답글 보기 클릭 완료')
        except:
            print('3. 답글 보기 없음')
        
        try:
            # 답글 더보기 클릭
            buttons_more = driver.find_elements(By.CSS_SELECTOR, '#continuation > yt-next-continuation > tp-yt-paper-button')
            for button in buttons_more:
                button.send_keys(Keys.ENTER)
                time.sleep(1)
            print('4. 답글 더보기 클릭 완료')
        except:
            print('4. 답글 더보기 없음')
        
        # 댓글 수집
        review_list = []
        reviews = driver.find_elements(By.CSS_SELECTOR, '#content-text')
        for review in reviews:
            review = review.text
            review_list.append(review)
        print('5. 댓글 수집 :', len(review_list))
            
    except:
        review_cnt = ''
        review_list = ''
        print('댓글 차단')
            
    target_info = {}
    target_info['제목'] = title
    target_info['조회수'] = view
    target_info['날짜'] = date
    target_info['좋아요'] = like
    target_info['싫어요'] = dont_like
    target_info['댓글 수'] = review_cnt
    target_info['댓글'] = review_list

    dict[count] = target_info

    driver.close()
    count += 1
    time.sleep(1)

  0%|          | 0/10 [00:38<?, ?it/s]

1


AttributeError: 'list' object has no attribute 'click'

In [18]:
!pip install pytube


                                              0.0/57.6 kB ? eta -:--:--
     -------------                          20.5/57.6 kB 320.0 kB/s eta 0:00:01
     --------------------                   30.7/57.6 kB 325.1 kB/s eta 0:00:01
     --------------------                   30.7/57.6 kB 325.1 kB/s eta 0:00:01
     ---------------------------------      51.2/57.6 kB 238.1 kB/s eta 0:00:01
     -------------------------------------- 57.6/57.6 kB 233.3 kB/s eta 0:00:00


In [2]:
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
import time
from openpyxl import Workbook
from openpyxl import load_workbook
from openpyxl.styles import Alignment
from pytube import YouTube
import datetime

In [40]:
df = pd.DataFrame(columns=['제목', 'URL', '조회수', '업데이트 날짜', '영상 길이'])
# 크롬 웹브라우저 실행
# driver = webdriver.Chrome(ChromeDriverManager().install())
driver = webdriver.Chrome("chromedriver-win64/chromedriver.exe")

keyword = '오킹'
# 키워드로 접속
driver.get(f"https://www.youtube.com/results?search_query={keyword}")
time.sleep(2)


# titles = driver.find_elements(By.CSS_SELECTOR, "#dismissible.style-scope.ytd-video-renderer")

driver.find_element(By.XPATH, '//*[@id="avatar-section"]/a').click() # 채널 클릭
time.sleep(1)
driver.find_element(By.XPATH, '//*[@id="tabsContent"]/tp-yt-paper-tab[2]').click() # 동영상 목록 클릭


C:\Users\Mgyu\AppData\Local\Temp\ipykernel_27548\748376928.py:4: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("chromedriver-win64/chromedriver.exe")


In [32]:
len(driver.find_elements(By.XPATH, '//*[@id="contents"]'))

17

In [41]:
html0 = driver.page_source
html = BeautifulSoup(html0,'html.parser')
video_list0 = html.find('div',{'id':'items'})
video_list2 = video_list0.find_all('ytd-grid-video-renderer',{'class':'style-scope ytd-grid-renderer'})
base_url = 'http://www.youtube.com' #영상별url이 유튜브 기본 url을 포함하지 않기 때문에 꼭 확인해줘야 함
url = []
for i in range(len(video_list2)):
    url = base_url+video_list2[i].find('a',{'id':'thumbnail'})['href']
    url.append(url)
# start_url = url[0] #리스트로 만들어져 있는 url중 한개의 url을 이용

# browser.get(start_url) 
# body = browser.find_element_by_tag_name('body')
# #웹드라이버로 url접속한 뒤 스크롤 내리기 위한 소스를 받아오는 것

In [47]:
html = driver.page_source
soup = BeautifulSoup(html, 'lxml')
video_list0 = soup.find('div', {'id': 'contents'})
video_list2 = video_list0.find_all('ytd-grid-video-renderer',{'class':'style-scope ytd-grid-renderer'})

base_url = 'http://www.youtube.com'
video_url = []

# 반복문을 실행시켜 비디오의 주소를 video_url에 넣는다.
for i in range(len(video_list2)):
    url = base_url+video_list2[i].find('a',{'id':'thumbnail'})['href']
    video_url.append(url)


In [50]:
video_list0

<div class="style-scope ytd-section-list-renderer" id="contents"><ytd-item-section-renderer class="style-scope ytd-section-list-renderer" top-spacing-zero="" use-height-hack=""><!--css-build:shady--><!--css-build:shady--><div class="style-scope ytd-item-section-renderer style-scope ytd-item-section-renderer" id="header"></div>
<div class="style-scope ytd-item-section-renderer" id="spinner-container">
<tp-yt-paper-spinner-lite aria-hidden="true" class="style-scope ytd-item-section-renderer"><!--css-build:shady--><div class="style-scope tp-yt-paper-spinner-lite" id="spinnerContainer"><div class="spinner-layer style-scope tp-yt-paper-spinner-lite"><div class="circle-clipper left style-scope tp-yt-paper-spinner-lite"><div class="circle style-scope tp-yt-paper-spinner-lite"></div></div><div class="circle-clipper right style-scope tp-yt-paper-spinner-lite"><div class="circle style-scope tp-yt-paper-spinner-lite"></div></div></div></div></tp-yt-paper-spinner-lite>
</div>
<div class="style-sco

In [44]:
html

<html dark="" darker-dark-theme="" darker-dark-theme-deprecate="" lang="ko-KR" style="font-size: 10px;font-family: Roboto, Arial, sans-serif;" system-icons="" typography="" typography-spacing=""><head><script data-original-src="/s/player/7ee36b0e/player_ias.vflset/ko_KR/miniplayer.js" nonce="y1yQC8One5sKO7MxOCe0cg" src="/s/player/7ee36b0e/player_ias.vflset/ko_KR/miniplayer.js"></script><script data-original-src="/s/player/7ee36b0e/player_ias.vflset/ko_KR/offline.js" nonce="y1yQC8One5sKO7MxOCe0cg" src="/s/player/7ee36b0e/player_ias.vflset/ko_KR/offline.js"></script><script data-original-src="/s/player/7ee36b0e/player_ias.vflset/ko_KR/endscreen.js" nonce="y1yQC8One5sKO7MxOCe0cg" src="/s/player/7ee36b0e/player_ias.vflset/ko_KR/endscreen.js"></script><script data-original-src="/s/player/7ee36b0e/player_ias.vflset/ko_KR/captions.js" nonce="y1yQC8One5sKO7MxOCe0cg" src="/s/player/7ee36b0e/player_ias.vflset/ko_KR/captions.js"></script><script data-original-src="/s/player/7ee36b0e/player_ias.vf

In [ ]:
html = driver.page_source
    soup = BeautifulSoup(html, 'lxml')
 
    video_list0 = soup.find('div', {'id': 'contents'})
    video_list2 = video_list0.find_all('ytd-grid-video-renderer',{'class':'style-scope ytd-grid-renderer'})
 
    base_url = 'http://www.youtube.com'
    video_url = []
 
    # 반복문을 실행시켜 비디오의 주소를 video_url에 넣는다.
    for i in range(len(video_list2)):
        url = base_url+video_list2[i].find('a',{'id':'thumbnail'})['href']
        video_url.append(url)

In [33]:
# titles = driver.find_elements(By.CSS_SELECTOR, "#dismissible.style-scope.ytd-video-renderer")
titles = driver.find_elements(By.XPATH, '//*[@id="contents"]')
for title in titles:

    main_title = title.find_element(By.CSS_SELECTOR, "#video-title").get_property("title")

    tube_url = title.find_element(By.CSS_SELECTOR, "#video-title").get_property("href")

    df.loc[len(df), ['제목', 'URL']] =  [main_title, tube_url]
df

제목  \
0   요즘 세상엔 경찰 공권력이 높아져야 한다고 봅니다..   
1   요즘 세상엔 경찰 공권력이 높아져야 한다고 봅니다..   
2   요즘 세상엔 경찰 공권력이 높아져야 한다고 봅니다..   
3             남자들은 옷을 왜 이렇게 입을까요?   
4              부산에서 잡채밥보다 더 놀랐던 것   
..                            ...   
80                                  
81                                  
82                                  
83                                  
84                                  

                                                  URL  조회수 업데이트 날짜 영상 길이  
0   https://www.youtube.com/watch?v=YMNmHaC28A4&pp...  NaN     NaN   NaN  
1   https://www.youtube.com/watch?v=YMNmHaC28A4&pp...  NaN     NaN   NaN  
2   https://www.youtube.com/watch?v=YMNmHaC28A4&pp...  NaN     NaN   NaN  
3   https://www.youtube.com/watch?v=y7tbBvx4Z3Y&pp...  NaN     NaN   NaN  
4   https://www.youtube.com/watch?v=qXoUaN3g5V4&pp...  NaN     NaN   NaN  
..                                                ...  ...     ...   ...  
80                                               None  NaN     NaN   NaN  
81                                               None  NaN     NaN   NaN  
82                                               None  NaN     NaN   NaN  
83                                               None  NaN     NaN   NaN  
84                                               None  NaN     NaN   NaN  

[85 rows x 5 columns]

In [5]:
for i in range(len(df)):

    url = df.iloc[i,1]
    tube = YouTube(url)

    view = tube.views # 조회수 불러오기
    update_dates = str(tube.publish_date)  # 업데이트 날짜 불러와서 str 형태로 변환
    update_date = update_dates.split(" ")  # 업데이트 날짜 string을 공백으로 분리

    # 업데이트 날짜는 0000-00-00 00-00-00 형태인데 앞의 날짜부분만 추출하려 합니다.
    length_second = int(tube.length) # 유튜브 영상의 길이를 불러옴(문자 형태인것 같아서 int로 변환) / 문자가 아닐 수도...
    length = str(datetime.timedelta(seconds=length_second)) # datetime 모듈의 timedelta 함수로 초를 시:분:초 로 변환
    
    df.iloc[i, 2] = view 
    df.iloc[i, 3] = update_date[0] # 추출한 날짜 중 앞의 날짜부분만 추출
    df.iloc[i, 4] = length
df

제목  \
0                       요즘 세상엔 경찰 공권력이 높아져야 한다고 봅니다..   
1                                   남의 일에 끼지 좀 마세요 제발   
2                                     ENFP의 망상 동화 만들기   
3                                       북한 간첩이 교육받는 법   
4                       출연료 미지급 대표님 지급하시겠다는 날짜가 지났네요?   
5                                예습하고 오펜하이머를 봐야 하는 이유   
6                                해병대 대민지원 안타까운 사고에 대해   
7                               야동 안 본다고 하는 사람들 조심하세요   
8                                  부산에서 잡채밥보다 더 놀랐던 것   
9                               사실 제가 살찐 이유는 따로 있었습니다   
10                                   이해하기 어려운 여자들의 세계   
11                                남자들은 옷을 왜 이렇게 입을까요?   
12                                북한이 핵을 절대 쏘지 못하는 이유   
13                                    드라마를 클립으로만 본 사람   
14                               여자친구가 번호 따였을 때의 내 심정   
15                                상남자는 질병 따위에 지지 않습니다   
16                                     MBTI T와 F의 차이점   
17                                  세계에서 가장 큰 귀신의 집..   
18  [ENG SUB] 심성, 품성, 인성 그리고 타고난 DNA까지 갖춘 예능 대부 🤴킹...   
19                          요즘 남사친 여사친 문제 노래로도 시비 거네요   
20                                     군필자가 본 DP 시즌 2   
21                                자영업자분들에게 존경심을 느꼈습니다   
22                    푸켓 피피섬에서 배우는 스쿠버 다이빙 [푸켓  ep.1]   
23                                      그림도네 보러올래..?♥   
24                                 미용사분들께 드릴 말씀이 있습니다   
25                                      롯데리아 신메뉴 먹어보기   

                                                  URL      조회수     업데이트 날짜  \
0   https://www.youtube.com/watch?v=YMNmHaC28A4&pp...   249295  2023-09-06   
1   https://www.youtube.com/watch?v=W0I6RA92Qj0&pp...   225329  2023-09-05   
2   https://www.youtube.com/watch?v=gWJ4K-ty6ng&pp...   576549  2023-03-26   
3   https://www.youtube.com/watch?v=k644AtDkYbY&pp...   616695  2023-06-14   
4   https://www.youtube.com/watch?v=7r5TPIEaGNk&pp...   846977  2023-09-03   
5   https://www.youtube.com/watch?v=8IKuK_yVkgk&pp...   189921  2023-09-04   
6   https://www.youtube.com/watch?v=46Lq8Ak9rJ8&pp...   415388  2023-08-30   
7   https://www.youtube.com/watch?v=y_jsV17DKAA&pp...   550001  2023-08-31   
8   https://www.youtube.com/watch?v=qXoUaN3g5V4&pp...   578216  2023-03-31   
9   https://www.youtube.com/watch?v=NtggbKXzXr4&pp...   644174  2023-05-21   
10  https://www.youtube.com/watch?v=IuJPvdGtVjk&pp...   928955  2023-04-12   
11  https://www.youtube.com/watch?v=y7tbBvx4Z3Y&pp...   688773  2023-02-10   
12  https://www.youtube.com/watch?v=G5hk1UBLtRk&pp...  1252033  2022-08-20   
13  https://www.youtube.com/watch?v=8a7Ob4m9zcA&pp...   508103  2023-07-07   
14  https://www.youtube.com/watch?v=5rkT4KdLaSY&pp...   439598  2023-08-27   
15  https://www.youtube.com/watch?v=fRNrJAS20Ws&pp...   208841  2023-08-28   
16  https://www.youtube.com/watch?v=QlwMt0Y6eSo&pp...   592556  2023-07-23   
17  https://www.youtube.com/watch?v=vJoT0_zIvdw&pp...   498952  2023-05-31   
18  https://www.youtube.com/watch?v=dmzMK5eY4jg&pp...   766201  2023-05-27   
19  https://www.youtube.com/watch?v=17nAttXAYOs&pp...   246386  2023-08-29   
20  https://www.youtube.com/watch?v=YdYoACS1Ge8&pp...   661213  2023-08-23   
21  https://www.youtube.com/watch?v=X4hPXRl428g&pp...   221867  2023-08-18   
22  https://www.youtube.com/watch?v=9kmGxKbex0k&pp...   235042  2023-07-30   
23  https://www.youtube.com/watch?v=ZrOBlecpW1c&pp...   826294  2023-04-26   
24  https://www.youtube.com/watch?v=Di59YX72O1E&pp...   309206  2023-08-10   
25  https://www.youtube.com/watch?v=Z-wkuJNpFWE&pp...   276421  2023-08-22   

      영상 길이  
0   0:08:41  
1   0:08:53  
2   0:09:37  
3   0:08:42  
4   0:12:06  
5   0:09:43  
6   0:10:38  
7   0:08:51  
8   0:10:23  
9   0:09:04  
10  0:11:44  
11  0:11:31  
12  0:11:19  
13  0:09:34  
14  0:09:10  
15  0:09:48  
16  0:10:06  
17  0:15:01  
18  0:13:36  
19  0:17:41  
20  0:10:58  
21  0:08:44  
22  0:19:21  
23  0:10:12  
24  0:09:17  
25  0:12:11

In [46]:
# https://pytube.io/
print("제목 : ", tube.title)
print("길이 : ", tube.length)
print("게시자 : ", tube.author)
print("게시날짜 : ", tube.publish_date)
print("조회수 : ", tube.views)
print("키워드 : ", tube.keywords)
print("설명 : ", tube.description)
print("썸네일 : ", tube.thumbnail_url)

제목 :  남자들은 옷을 왜 이렇게 입을까요?
길이 :  691
게시자 :  오킹TV
게시날짜 :  2023-02-10 00:00:00
조회수 :  687886
키워드 :  []
설명 :  None
썸네일 :  https://i.ytimg.com/vi/y7tbBvx4Z3Y/hq720.jpg


In [42]:
df

제목  \
0               남의 일에 끼지 좀 마세요 제발   
1            예습하고 오펜하이머를 봐야 하는 이유   
2   출연료 미지급 대표님 지급하시겠다는 날짜가 지났네요?   
3                 ENFP의 망상 동화 만들기   
4           부당하게 택시비 추가 요청을 받았습니다   
5                   북한 간첩이 교육받는 법   
6                이해하기 어려운 여자들의 세계   
7             남자들은 옷을 왜 이렇게 입을까요?   
8                 드라마를 클립으로만 본 사람   
9           여자친구가 취했는데 연락이 안 된다고?   
10        광고에 미친 두찜놈들한테 따지러 간 미친놈   
11       출연료 미지급 대표님 새로운 기사 내셨네요?   
12           여자친구가 번호 따였을 때의 내 심정   
13             부산에서 잡채밥보다 더 놀랐던 것   
14          야동 안 본다고 하는 사람들 조심하세요   
15          사실 제가 살찐 이유는 따로 있었습니다   

                                                  URL     조회수     업데이트 날짜  \
0   https://www.youtube.com/watch?v=W0I6RA92Qj0&pp...  194159  2023-09-05   
1   https://www.youtube.com/watch?v=8IKuK_yVkgk&pp...  179739  2023-09-04   
2   https://www.youtube.com/watch?v=7r5TPIEaGNk&pp...  811992  2023-09-03   
3   https://www.youtube.com/watch?v=gWJ4K-ty6ng&pp...  574895  2023-03-26   
4   https://www.youtube.com/watch?v=7wysOQUH1SM&pp...  415522  2023-03-25   
5   https://www.youtube.com/watch?v=k644AtDkYbY&pp...  615477  2023-06-14   
6   https://www.youtube.com/watch?v=IuJPvdGtVjk&pp...  927112  2023-04-12   
7   https://www.youtube.com/watch?v=y7tbBvx4Z3Y&pp...  687879  2023-02-10   
8   https://www.youtube.com/watch?v=8a7Ob4m9zcA&pp...  507386  2023-07-07   
9   https://www.youtube.com/watch?v=Sal4OAZAhMc&pp...  507062  2023-06-04   
10  https://www.youtube.com/watch?v=dii7OTaQsSw&pp...  257893  2023-08-26   
11  https://www.youtube.com/watch?v=FMg27cq22wU&pp...  662851  2023-08-24   
12  https://www.youtube.com/watch?v=5rkT4KdLaSY&pp...  435899  2023-08-27   
13  https://www.youtube.com/watch?v=qXoUaN3g5V4&pp...  577490  2023-03-31   
14  https://www.youtube.com/watch?v=y_jsV17DKAA&pp...  534914  2023-08-31   
15  https://www.youtube.com/watch?v=NtggbKXzXr4&pp...  643461  2023-05-21   

      영상 길이  
0   0:08:53  
1   0:09:43  
2   0:12:06  
3   0:09:37  
4   0:08:25  
5   0:08:42  
6   0:11:44  
7   0:11:31  
8   0:09:34  
9   0:09:26  
10  0:20:51  
11  0:08:18  
12  0:09:10  
13  0:10:23  
14  0:08:51  
15  0:09:04

In [61]:
url

'https://www.youtube.com/watch?v=W0I6RA92Qj0&pp=ygUG7Jik7YK5'

In [63]:
from selenium.webdriver.common.by import By
driver = webdriver.Chrome("chromedriver-win64/chromedriver.exe")

for i in range(len(df)):
    url = df.iloc[i,1]
    driver.get(url)
    time.sleep(2)
    driver.maximize_window() 
    body = driver.find_element("tag name", "body")
    
    time.sleep(1.5)#브라우저 로딩시간기다려야함
    
    num_of_pagedowns = 4 #page_down은 2로 놔도 괜찮을 듯 최대화 했으므로
    while num_of_pagedowns:
        body.send_keys(Keys.PAGE_DOWN)
        time.sleep(1.5) #스크롤 속도를 지정할 수 있는 것인데  1.5초가 가장 적당할 듯 1초면 너무 빠름
        #현재는 스크롤을 7번만 하도록 설정되어 있으나 이후에 댓글을 크롤링하기 위해서는 스크롤을 댓글이 안보
        #일때까지 내리면 될텐데 시간이 엄청 오래 걸릴 것임 - 따라서 적당한 수준의 댓글을 크롤링하는것이 좋음
        num_of_pagedowns -= 1
    #여기에 time.sleep를 집어 넣는 방법을 고안
    html0 = driver.page_source
    html = BeautifulSoup(html0,'html.parser')
    
    start_date = html.find('span',{'class':'date style-scope ytd-video-secondary-info-renderer'}).text
    comment = html.find('h2',{'id':'count'}).find('yt-formatted-string').text
    
    #좋아요수
    likes_num = html.find('yt-formatted-string',{'id':'text','class':'style-scope ytd-toggle-button-renderer style-text','aria-label':re.compile('좋아요')}).text+'개'

    #싫어요수
    unlikes_num = html.find('yt-formatted-string',{'id':'text','class':'style-scope ytd-toggle-button-renderer style-text','aria-label':re.compile('싫어요')}).text+'개'

    insert_data = pd.DataFrame({'name':[name],
                     'thumbnail':[thum],
                     'view':[view],
                     'previous_time':[previous],
                     'video_url':[url],
                     'start_date':[start_date],
                     'comment':[comment],
                     'likes_num':[likes_num],
                     'unlikes_num':[unlikes_num]})
    
    isabe = isabe.append(insert_data)
isabe.index = range(len(isabe))

C:\Users\Mgyu\AppData\Local\Temp\ipykernel_24556\4143278503.py:2: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("chromedriver-win64/chromedriver.exe")


NameError: name 'BeautifulSoup' is not defined

In [1]:
import pandas as pd
from bs4 import BeautifulSoup
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from tqdm import tqdm
import time
import re
import requests
import random


#Queue의 기본적인 기능 구현
class Queue():
    def __init__(self, maxsize):
        self.queue = []
        self.maxsize = maxsize
        
    # Queue에 Data 넣음
    def enqueue(self, data):
        self.queue.append(data)

    # Queue에 가장 먼저 들어온 Data 내보냄
    def dequeue(self):
        dequeue_object = None
        if self.isEmpty():
            print("Queue is Empty")
        else:
            dequeue_object = self.queue[0]
            self.queue = self.queue[1:]
        return dequeue_object
    
    # Queue에 가장 먼저들어온 Data return
    def peek(self):
        peek_object = None
        if self.isEmpty():
            print("Queue is Empty")
        else:
            peek_object = self.queue[0]
        return peek_object
    
    # Queue가 비어있는지 확인
    def isEmpty(self):
        is_empty = False
        if len(self.queue) == 0:
            is_empty = True
        return is_empty
    
    # Queue의 Size가 Max Size를 초과하는지 확인
    def isMaxSizeOver(self):
        queue_size = len(self.queue)
        if (queue_size > self.maxsize):
            return False
        else :
            return True

In [ ]:
if __name__=="__main__":
    #set option of selenium
    options = webdriver.ChromeOptions()
    options.add_argument('window-size=1920x1080')
    options.add_argument('disable-gpu')
    options.add_argument('user')
    options.add_argument("user-agent=Mozilla/5.0 (Macintosh; Intel Mac OS X 10_12_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/61.0.3163.100 Safari/537.36")
    options.add_argument("lang=ko_KR")
    # driver = webdriver.Chrome(ChromeDriverManager().install(), chrome_options=options)
    driver = webdriver.Chrome("chromedriver-win64/chromedriver.exe")
    
    #target of crawling
    data_list = []
    driver.get(url)
    
    #페이지 Open 후 기다리는 시간
    time.sleep(5.0)

    #down the scroll
    body = driver.find_element_by_tag_name('body')
    last_page_height = driver.execute_script("return document.documentElement.scrollHeight")
    
    # max size 50의 Queue 생성
    # 0.1sec * 50 = 5sec 동안 Scroll 업데이트가 없으면 스크롤 내리기 종료
    szQ = Queue(50)
    enqueue_count = 0
    
    while True:
        # Scroll 내리기
        driver.execute_script("window.scrollTo(0, document.documentElement.scrollHeight);")
        
        # Scroll Height를 가져오는 주기
        time.sleep(0.1)
        new_page_height = driver.execute_script("return document.documentElement.scrollHeight")
        
        # Queue가 꽉 차는 경우 스크롤 내리기 종료
        if(enqueue_count > szQ.maxsize):
            break
        
        # 첫 Loop 수행 (Queue가 비어있는 경우) 예외 처리
        if(szQ.isEmpty()) :
            szQ.enqueue(new_page_height)
            enqueue_count += 1
            
        # Queue에 가장 먼저 들어온 데이터와 새로 업데이트 된 Scroll Height를 비교함
        # 같으면 그대로 Enqueue, 다르면 Queue의 모든 Data를 Dequeue 후 새로운 Scroll Height를 Enqueue 함.    
        else :
            if(szQ.peek() == new_page_height) :
                szQ.enqueue(new_page_height)
                enqueue_count += 1
            else :
                szQ.enqueue(new_page_height)
                for z in range(enqueue_count) :
                    szQ.dequeue()
                enqueue_count = 1
        
        # 기존의 Scroll 내리는 방식      
        #if new_page_height == last_page_height:
        #    break
        #last_page_height = new_page_height
        #time.sleep(2.0)
    
    # print ("[PASS] Get all comments of URL")

    html0 = driver.page_source
    driver.close()
    html = BeautifulSoup(html0, 'html.parser')

    comments_list = html.findAll('ytd-comment-thread-renderer', {'class':'style-scope ytd-item-section-renderer'})
    # print (comments_list)


    for j in range(len(comments_list)):
     #contents of comment
        comment = comments_list[j].find('yt-formatted-string',{'id':'content-text'}).text
        comment = comment.replace('\n', '') 
        comment = comment.replace('\t', '')
        #print(comment) 
        youtube_id = comments_list[j].find('a', {'id': 'author-text'}).span.text
        youtube_id = youtube_id.replace('\n', '') 
        youtube_id = youtube_id.replace('\t', '') 
        youtube_id = youtube_id.strip()
    
        raw_date = comments_list[j].find('yt-formatted-string', { 'class': 'published-time-text above-comment style-scope ytd-comment-renderer'})
        date = raw_date.a.text
    
        try:
            like_num = comments_list[j].find('span', {'id': 'vote-count-middle', 'class': 'style-scope ytd-comment-action-buttons-renderer', 'aria-label': re.compile('좋아요')}).text
            like_num = like_num.replace('\n', '') 
            like_num = like_num.replace('\t', '')
            like_num = like_num.strip()
        except: like_num = 0
    
        data = {'youtube_id': youtube_id, 'comment': comment, 'date': date, 'like_num': like_num}
        data_list.append(data)
    
    result_df = pd.DataFrame(data_list, columns=['youtube_id','comment','date','like_num'])    
    result_df.to_excel("./Excel_Data/data.xlsx", index = False)